# Install dependencies

In [1]:
%load_ext autoreload
%autoreload 2
import sys
import plotly.io as io
io.templates.default = 'plotly_white'
# # enable modules import
# sys.path.insert(1, '/kaggle/input/modules')

# decade
decade = [2000, 2010]

# Load and preprocess data

In [2]:
from modules.spark_preprocess import SparkSPreprocessor

# SparkPreprocessor read the big csv file and convert it in the more convenient format parquet
#
sp = SparkSPreprocessor("song_lyrics.csv","./data/", "20g")


23/06/03 20:15:44 WARN Utils: Your hostname, thomas-ThinkPad-T490 resolves to a loopback address: 127.0.1.1; using 192.168.31.207 instead (on interface wlp0s20f3)
23/06/03 20:15:44 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
23/06/03 20:15:46 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


In [3]:
df = sp.preprocess_data(freq=0.01, seed = 42, sample_by = 'ddecade')

In [4]:
# load data
import pandas as pd

df = pd.read_csv('./data/preprocessed_data.csv')
len(df)

4308

In [5]:
from modules.preprocess_text import clean_lyrics

df = df[df['decade'].isin(decade)]
df = clean_lyrics(df)
len(df)

1078

# Text preprocessing

In [6]:
import spacy
from modules.preprocess_text import ngram_models, ngram_preprocess

# gpu off
print("set gpu: ", spacy.prefer_gpu())

new_nlp = spacy.load('en_core_web_sm')

# get bigram_model
bigram_model, trigram_model = ngram_models(df)

# set personalised stop words
new_stop_words = {
    'like','know','come','get', 'got',
    'go','to','oh','yeah','la', 'lala', 'lalala','ooh','yeah',
    'hey','whoa','woah', 'ohh', 'was', 'mmm',
    'oooh','yah','yeh','mmm', 'hmm','deh','doh','jah','wa',
} 

set gpu:  False


# Grid search based on LDA

In [7]:
from modules.lda_models import LDATopicModeling
import logging

gensim_log = './gensim.log'

with open(gensim_log, 'w'):
    pass

# Remove all handlers associated with the root logger object.
for handler in logging.root.handlers[:]:
    logging.root.removeHandler(handler)

#initiate log file
logging.basicConfig(
    filename = gensim_log,
    filemode = 'r+',
    format='%(asctime)s:%(levelname)s:%(message)s',
    level=logging.INFO)

ngram_model = LDATopicModeling(
    df,
    gensim_log=gensim_log,
    decade = decade,
    directory = "./models/",
    lang_preprocess = lambda x : ngram_preprocess(
                        x, new_nlp, bigram_model,
                        trigram_model, new_stop_words),
    grid_search = True,
    n_topics=20,
    chunks=2000,
    worker_nodes=4)

total lda computation:  32
coherence cv:0.2897663113836216, coherence umass:-1.9068068350171288
alpha:symmetric
eta:symmetric
topic:5
coherence cv:0.3563558309656766, coherence umass:-1.8021411961196794
alpha:asymmetric
eta:symmetric
topic:5
coherence cv:0.3447801794915762, coherence umass:-2.910705849977259
alpha:symmetric
eta:symmetric
topic:6
coherence cv:0.33535898292023253, coherence umass:-2.667348514284416
alpha:asymmetric
eta:symmetric
topic:6
coherence cv:0.3242092774065381, coherence umass:-2.2566498159804405
alpha:symmetric
eta:symmetric
topic:7
coherence cv:0.3088190968785892, coherence umass:-2.2883956094283517
alpha:asymmetric
eta:symmetric
topic:7
coherence cv:0.31727709972883644, coherence umass:-2.330358657300537
alpha:symmetric
eta:symmetric
topic:8
coherence cv:0.31341632878850867, coherence umass:-2.965881023122453
alpha:asymmetric
eta:symmetric
topic:8
coherence cv:0.3152761768257226, coherence umass:-2.2400118466260306
alpha:symmetric
eta:symmetric
topic:9
coheren

In [8]:
ngram_model.plot_tsne(2)

[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 1078 samples in 0.012s...
[t-SNE] Computed neighbors for 1078 samples in 0.047s...
[t-SNE] Computed conditional probabilities for sample 1000 / 1078
[t-SNE] Computed conditional probabilities for sample 1078 / 1078
[t-SNE] Mean sigma: 0.009663
[t-SNE] KL divergence after 250 iterations with early exaggeration: 57.911465
[t-SNE] KL divergence after 1000 iterations: 0.403649


In [9]:
ngram_model.dashboard_LDAvis()

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
10     0.114185  0.029027       1        1  18.972308
11     0.098268 -0.187723       2        1  16.110966
5      0.085650  0.146261       3        1  11.797183
9      0.047791  0.004343       4        1  10.836158
1      0.032590  0.027353       5        1   7.925046
7      0.037798  0.004564       6        1   7.924285
4      0.011960  0.128268       7        1   7.324379
8      0.013745 -0.118621       8        1   5.839202
2     -0.027477 -0.023103       9        1   4.702922
6     -0.081424 -0.013117      10        1   3.075443
3     -0.128497  0.003807      11        1   2.830720
0     -0.204591 -0.001059      12        1   2.661388, topic_info=       Term         Freq        Total Category  logprob  loglift
34     love  1053.000000  1053.000000  Default  30.0000  30.0000
364   nigga   368.000000   368.000000  Default  29.0000  29.0000
355    good   390.000000   390.000000  Default  28.0000  28.0000
6     bitch   388.000000   388.000000  Default  27.0000  27.0000
0      baby   461.000000   461.000000  Default  26.0000  26.0000
...     ...          ...          ...      ...      ...      ...
604    year     6.499216   140.983965  Topic12  -5.6879   0.5494
2070   help     5.451971    38.409605  Topic12  -5.8636   1.6740
906   sweet     5.873179    88.160398  Topic12  -5.7892   0.9176
245    work     5.876350   118.041051  Topic12  -5.7886   0.6262
313    tell     5.844036   112.398884  Topic12  -5.7942   0.6697

[889 rows x 6 columns], token_table=      Topic      Freq         Term
term                              
6765      8  0.222939      absence
6765     12  0.668816      absence
5893     12  0.675989        absii
7494     11  0.441085   absolutely
5274      9  0.625031          act
...     ...       ...          ...
524       7  0.032124        young
524       8  0.149910        young
524      12  0.182034        young
2292      8  0.909191  yourselfcan
1152      2  0.929737     yukmouth

[2647 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[11, 12, 6, 10, 2, 8, 5, 9, 3, 7, 4, 1])

In [10]:
ngram_model.plot_likelihood(30)

In [11]:
ngram_model.plot_coherence()

In [12]:
ngram_model.get_cv_results

topics       alpha        eta       c_v    u_mass
0        5   symmetric  symmetric  0.289766 -1.906807
1        5  asymmetric  symmetric  0.356356 -1.802141
2        6   symmetric  symmetric  0.344780 -2.910706
3        6  asymmetric  symmetric  0.335359 -2.667349
4        7   symmetric  symmetric  0.324209 -2.256650
5        7  asymmetric  symmetric  0.308819 -2.288396
6        8   symmetric  symmetric  0.317277 -2.330359
7        8  asymmetric  symmetric  0.313416 -2.965881
8        9   symmetric  symmetric  0.315276 -2.240012
9        9  asymmetric  symmetric  0.311518 -2.766915
10      10   symmetric  symmetric  0.338159 -3.087946
11      10  asymmetric  symmetric  0.340532 -2.433033
12      11   symmetric  symmetric  0.319140 -2.921369
13      11  asymmetric  symmetric  0.308769 -2.568447
14      12   symmetric  symmetric  0.382662 -4.302568
15      12  asymmetric  symmetric  0.318578 -3.266121
16      13   symmetric  symmetric  0.329208 -2.775813
17      13  asymmetric  symmetric  0.337536 -3.179117
18      14   symmetric  symmetric  0.332860 -3.326633
19      14  asymmetric  symmetric  0.312334 -2.830272
20      15   symmetric  symmetric  0.312712 -3.354003
21      15  asymmetric  symmetric  0.348992 -3.468976
22      16   symmetric  symmetric  0.313499 -3.035126
23      16  asymmetric  symmetric  0.336228 -3.483592
24      17   symmetric  symmetric  0.328707 -3.887822
25      17  asymmetric  symmetric  0.320149 -3.358482
26      18   symmetric  symmetric  0.330305 -3.760458
27      18  asymmetric  symmetric  0.333786 -3.273771
28      19   symmetric  symmetric  0.338158 -4.142495
29      19  asymmetric  symmetric  0.325621 -3.341994
30      20   symmetric  symmetric  0.306392 -3.337256
31      20  asymmetric  symmetric  0.326269 -4.056897

In [13]:
ngram_model.dashboard()

[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 1078 samples in 0.001s...
[t-SNE] Computed neighbors for 1078 samples in 0.042s...
[t-SNE] Computed conditional probabilities for sample 1000 / 1078
[t-SNE] Computed conditional probabilities for sample 1078 / 1078
[t-SNE] Mean sigma: 0.009644
[t-SNE] KL divergence after 250 iterations with early exaggeration: 57.762741
[t-SNE] KL divergence after 1000 iterations: 0.401526


In [14]:
ngram_model.save_current_model()

# U_MASS Coherence grid search

In [15]:
ngram_model = LDATopicModeling(
    df,
    gensim_log=gensim_log,
    decade = decade,
    lang_preprocess = lambda x : ngram_preprocess(
                        x, new_nlp, bigram_model,
                        trigram_model, new_stop_words),
    grid_search = True,
    n_topics=20,
    chunks=2000,
    directory = "./models/",
    metric='u_mass',
    worker_nodes=4)

total lda computation:  32


KeyboardInterrupt: 

In [ ]:
ngram_model.plot_tsne(2)

[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 1078 samples in 0.001s...
[t-SNE] Computed neighbors for 1078 samples in 0.018s...
[t-SNE] Computed conditional probabilities for sample 1000 / 1078
[t-SNE] Computed conditional probabilities for sample 1078 / 1078
[t-SNE] Mean sigma: 0.001681
[t-SNE] KL divergence after 250 iterations with early exaggeration: 50.063606
[t-SNE] KL divergence after 1000 iterations: 0.225869


In [ ]:
ngram_model.dashboard_LDAvis()

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
0     -0.072321  0.039508       1        1  35.401256
1     -0.018215  0.035384       2        1  18.514633
4      0.157161 -0.044884       3        1  18.130659
3     -0.090815 -0.098097       4        1  14.088435
2      0.024190  0.068089       5        1  13.865016, topic_info=       Term        Freq       Total Category  logprob  loglift
6     bitch  370.000000  370.000000  Default  30.0000  30.0000
364   nigga  351.000000  351.000000  Default  29.0000  29.0000
287  niggas  294.000000  294.000000  Default  28.0000  28.0000
34     love  991.000000  991.000000  Default  27.0000  27.0000
348    fuck  372.000000  372.000000  Default  26.0000  26.0000
..      ...         ...         ...      ...      ...      ...
25    heart   36.839015  495.793088   Topic5  -5.6035  -0.6238
66    thing   33.047322  349.599470   Topic5  -5.7122  -0.3830
320   wrong   25.713048  129.015412   Topic5  -5.9631   0.3629
160   light   27.878232  288.463639   Topic5  -5.8823  -0.3609
170    mind   24.899245  323.978960   Topic5  -5.9953  -0.5900

[407 rows x 6 columns], token_table=      Topic      Freq      Term
term                           
3975      5  0.940730     agony
1677      1  0.070031     ahead
1677      2  0.116718     ahead
1677      3  0.116718     ahead
1677      4  0.070031     ahead
...     ...       ...       ...
320       5  0.201526     wrong
8234      5  0.722530      yaaa
4200      5  0.722483      yooo
929       1  0.893919     youth
1152      2  0.878374  yukmouth

[822 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2, 5, 4, 3])

In [ ]:
ngram_model.plot_likelihood(30)

In [ ]:
ngram_model.plot_coherence()

In [ ]:
ngram_model.get_cv_results

topics       alpha        eta       c_v    u_mass
0        5   symmetric  symmetric  0.329910 -1.826272
1        5  asymmetric  symmetric  0.334278 -1.770744
2        6   symmetric  symmetric  0.323198 -1.981309
3        6  asymmetric  symmetric  0.289905 -2.137746
4        7   symmetric  symmetric  0.351197 -2.975774
5        7  asymmetric  symmetric  0.300282 -2.009404
6        8   symmetric  symmetric  0.352095 -2.654706
7        8  asymmetric  symmetric  0.320459 -2.193589
8        9   symmetric  symmetric  0.318636 -2.091282
9        9  asymmetric  symmetric  0.344218 -2.814635
10      10   symmetric  symmetric  0.342514 -3.452617
11      10  asymmetric  symmetric  0.342196 -3.618984
12      11   symmetric  symmetric  0.339589 -3.150226
13      11  asymmetric  symmetric  0.327506 -3.196346
14      12   symmetric  symmetric  0.330141 -2.879823
15      12  asymmetric  symmetric  0.296080 -2.788900
16      13   symmetric  symmetric  0.286463 -2.329647
17      13  asymmetric  symmetric  0.348979 -3.487828
18      14   symmetric  symmetric  0.327699 -3.649636
19      14  asymmetric  symmetric  0.306582 -2.950766
20      15   symmetric  symmetric  0.315497 -2.915360
21      15  asymmetric  symmetric  0.288134 -3.044482
22      16   symmetric  symmetric  0.333227 -3.617744
23      16  asymmetric  symmetric  0.306060 -2.908719
24      17   symmetric  symmetric  0.319719 -3.759656
25      17  asymmetric  symmetric  0.322503 -3.341516
26      18   symmetric  symmetric  0.323775 -3.656594
27      18  asymmetric  symmetric  0.326513 -3.708499
28      19   symmetric  symmetric  0.322480 -3.420913
29      19  asymmetric  symmetric  0.325841 -3.345391
30      20   symmetric  symmetric  0.324892 -3.588267
31      20  asymmetric  symmetric  0.332242 -4.085934

In [ ]:
ngram_model.dashboard()

[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 1078 samples in 0.001s...
[t-SNE] Computed neighbors for 1078 samples in 0.019s...
[t-SNE] Computed conditional probabilities for sample 1000 / 1078
[t-SNE] Computed conditional probabilities for sample 1078 / 1078
[t-SNE] Mean sigma: 0.001680
[t-SNE] KL divergence after 250 iterations with early exaggeration: 50.025101
[t-SNE] KL divergence after 1000 iterations: 0.226227


In [ ]:
ngram_model.save_current_model()

# Bertopic

Preprocess data before clustering (not advised by documentation).

In [ ]:
# lyrics preprocessing
preprocess_lyrics = df['lyrics'] \
    .apply(lambda x : ' '.join(
            ngram_preprocess(
            x, new_nlp, bigram_model, 
            trigram_model, new_stop_words)))

# clean lyrics
docs = preprocess_lyrics.values

In [ ]:
from sentence_transformers import SentenceTransformer
from bertopic import BERTopic
from hdbscan import HDBSCAN
from umap import UMAP

sentence_model = SentenceTransformer("all-MiniLM-L6-v2")
embeddings = sentence_model.encode(docs)

umap_model = UMAP(n_components=5, n_neighbors=15, min_dist=0.0)
hdbscan_model = HDBSCAN(min_samples=10, gen_min_span_tree=True)

# Train BERTopic
topic_model = BERTopic(nr_topics = 30, umap_model=umap_model, hdbscan_model=hdbscan_model).fit(docs, embeddings)

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/umap/distances.py:1063: NumbaDeprecationWarning:

The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/umap/distances.py:1071: NumbaDeprecationWarning:

The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/umap/distances.py

Batches:   0%|          | 0/34 [00:00<?, ?it/s]

In [ ]:
# Run the visualization with the original embeddings
topic_model.visualize_documents(docs, embeddings=embeddings)

# Reduce dimensionality of embeddings, this step is optional but much faster to perform iteratively:
reduced_embeddings = UMAP(n_neighbors=10, n_components=2, min_dist=0.0, metric='cosine').fit_transform(embeddings)

In [ ]:
topic_model.visualize_documents(docs,reduced_embeddings=reduced_embeddings)

In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_hierarchy()

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:350: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:351: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:352: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:353: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead



In [ ]:
topic_model.visualize_barchart()

In [ ]:
topic_model.visualize_heatmap()

In [ ]:
topic_model.visualize_term_rank()

In [ ]:
from modules.bertopic_models import compute_coherence

print('cv :',compute_coherence(topic_model, docs, topic_model.topics_, metric = 'c_v'))
print('umass :',compute_coherence(topic_model, docs, topic_model.topics_, metric = 'u_mass'))

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

In [ ]:
topics_per_class = topic_model.topics_per_class(docs, classes=df['tag'].tolist())
topic_model.visualize_topics_per_class(topics_per_class)

In [ ]:
from modules.bertopic_models import save_bertopic_model

save_bertopic_model(topic_model, filename = 'bertopic_prepro_', model_dir = "./models")

In [ ]:
from sklearn.feature_extraction.text import CountVectorizer

docs = df['lyrics'].values

# apply embeddings to doc
embeddings = sentence_model.encode(docs)

# Train BERTopic
vectorizer_model = CountVectorizer(
    stop_words=list(new_nlp.Defaults.stop_words | new_stop_words))

# Train BERTopic
topic_model = BERTopic(nr_topics = 30,vectorizer_model=vectorizer_model, umap_model=umap_model, hdbscan_model=hdbscan_model).fit(docs, embeddings)

Batches:   0%|          | 0/34 [00:00<?, ?it/s]

In [ ]:
# Run the visualization with the original embeddings
topic_model.visualize_documents(docs, embeddings=embeddings)

# Reduce dimensionality of embeddings, this step is optional but much faster to perform iteratively:
reduced_embeddings = UMAP(n_neighbors=10, n_components=2, min_dist=0.0, metric='cosine').fit_transform(embeddings)

In [ ]:
topic_model.visualize_documents(docs, reduced_embeddings=reduced_embeddings)

In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_hierarchy()

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:350: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:351: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:352: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:353: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead



In [ ]:
topic_model.visualize_barchart()

In [ ]:
topic_model.visualize_heatmap()

In [ ]:
topic_model.visualize_term_rank()

In [ ]:
print('cv :',compute_coherence(topic_model, docs, topic_model.topics_, metric = 'c_v'))
print('umass :',compute_coherence(topic_model, docs, topic_model.topics_, metric = 'u_mass'))

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

In [ ]:
topics_per_class = topic_model.topics_per_class(docs, classes=df['tag'].tolist())
topic_model.visualize_topics_per_class(topics_per_class)

In [ ]:
save_bertopic_model(topic_model, filename = 'bertopic_', model_dir = "./models")

In [ ]:
from sklearn import preprocessing
le = preprocessing.LabelEncoder()

le.fit(sorted(df['tag'].unique()))

y = le.transform(df['tag'].tolist())


In [ ]:
from bertopic.vectorizers import ClassTfidfTransformer

ctfidf_model = ClassTfidfTransformer(reduce_frequent_words=True)

topic_model = BERTopic(nr_topics = 30, verbose=True, ctfidf_model=ctfidf_model,
                       umap_model=umap_model, hdbscan_model=hdbscan_model).fit(docs, y=y, embeddings = embeddings)

2023-06-03 17:55:36,291 - BERTopic - Reduced dimensionality
2023-06-03 17:55:36,313 - BERTopic - Clustered reduced embeddings
2023-06-03 17:55:36,641 - BERTopic - Reduced number of topics from 5 to 5


In [ ]:
# Run the visualization with the original embeddings
topic_model.visualize_documents(docs, embeddings=embeddings)

# Reduce dimensionality of embeddings, this step is optional but much faster to perform iteratively:
reduced_embeddings = UMAP(n_neighbors=10, n_components=2, min_dist=0.0, metric='cosine').fit_transform(embeddings)

In [ ]:
topic_model.visualize_documents(docs, reduced_embeddings=reduced_embeddings)

In [ ]:
topic_model.visualize_hierarchy()

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:350: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:351: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:352: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead

/home/thomas/miniconda3/envs/genius-env/lib/python3.10/site-packages/plotly/figure_factory/_dendrogram.py:353: DeprecationWarning:

scipy.array is deprecated and will be removed in SciPy 2.0.0, use numpy.array instead



In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_barchart()

In [ ]:
topic_model.visualize_heatmap()

In [ ]:
topic_model.visualize_term_rank()

In [ ]:
topics_per_class = topic_model.topics_per_class(docs, classes=df['tag'].tolist())
topic_model.visualize_topics_per_class(topics_per_class)

5it [00:00, 20.22it/s]


In [ ]:
print('cv :',compute_coherence(topic_model, docs, topic_model.topics_, metric = 'c_v'))
print('umass :',compute_coherence(topic_model, docs, topic_model.topics_, metric = 'u_mass'))

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

In [ ]:
save_bertopic_model(topic_model, filename = 'bertopic_semsup_', model_dir = "./working/models")

# Bertopic with brunokreiner lyrics transformer

In [ ]:
from sentence_transformers import SentenceTransformer

lyrics_model = SentenceTransformer('brunokreiner/lyrics-bert')

# apply embeddings to doc
embeddings = lyrics_model.encode(docs)

# Train BERTopic
vectorizer_model = CountVectorizer(
    stop_words=list(new_nlp.Defaults.stop_words | new_stop_words))
topic_model = BERTopic(nr_topics = 30, vectorizer_model=vectorizer_model, umap_model=umap_model, hdbscan_model=hdbscan_model).fit(docs, embeddings)

Batches:   0%|          | 0/34 [00:00<?, ?it/s]

2023-06-03 17:56:22,838 - BERTopic - Reduced dimensionality
2023-06-03 17:56:22,876 - BERTopic - Clustered reduced embeddings
2023-06-03 17:56:23,222 - BERTopic - Reduced number of topics from 10 to 10


In [ ]:
# Run the visualization with the original embeddings
topic_model.visualize_documents(docs, embeddings=embeddings)

# Reduce dimensionality of embeddings, this step is optional but much faster to perform iteratively:
reduced_embeddings = UMAP(n_neighbors=10, n_components=2, min_dist=0.0, metric='cosine').fit_transform(embeddings)

In [ ]:
topic_model.visualize_documents(docs, reduced_embeddings=reduced_embeddings)

In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_barchart()

In [ ]:
topics_per_class = topic_model.topics_per_class(docs, classes=df['tag'].tolist())
topic_model.visualize_topics_per_class(topics_per_class)

In [ ]:
print('cv :',compute_coherence(topic_model, docs, topic_model.topics_, metric = 'c_v'))
print('umass :',compute_coherence(topic_model, docs, topic_model.topics_, metric = 'u_mass'))

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

In [ ]:
save_bertopic_model(topic_model, filename = 'bertopic_lyricsBert_', model_dir = "./models")